In [1]:
import pandas as pd
import numpy as np
import scipy.stats
from sklearn.metrics.pairwise import cosine_similarity

El modelo presentado en este notebook es un modelo de filtrado colaborativo que busca la similitud entre usuarios para realizar recomendaciones de productos.

El filtrado colaborativo hace recomendaciones basadas en interacciones entre el usuario y el producto en el pasado. La suposición detrás del algoritmo es que a usuarios similares les gustan productos similares.


In [2]:
df_review = pd.read_csv('Data/df_modelo.csv')

In [3]:
df_review

business_id                 user_id  \
0       0bPLkL0QhhPO5kt1_EXmNQ  z1Dfj8kz3KCArkXaIyaBIA   
1       0bPLkL0QhhPO5kt1_EXmNQ  HvgKiuV36e9SzNqeA5zOfA   
2       0bPLkL0QhhPO5kt1_EXmNQ  7BhiY0D84Lj04kjEWn5fIQ   
3       0bPLkL0QhhPO5kt1_EXmNQ  0EjWviHaYwdaMaD8VBOHWA   
4       0bPLkL0QhhPO5kt1_EXmNQ  E47ejL3krT1wG8NvgtJDgw   
...                        ...                     ...   
824895  esBGrrmuZzSiECyRBoKvvA  E2uJ62_uEUu5wz2EnZ9CgA   
824896  esBGrrmuZzSiECyRBoKvvA  8aE275qBmEVUjb_nrE65CQ   
824897  esBGrrmuZzSiECyRBoKvvA  4wMvgdEVpFLCIhFANNBvGA   
824898  esBGrrmuZzSiECyRBoKvvA  mbIemu2trEjtn8viGHD3dA   
824899  esBGrrmuZzSiECyRBoKvvA  rDtA_KBbjnPjsKDT0-itgA   

                     review_id  stars_x  stars_y  useful  funny  cool  \
0       oTTuahWNWzX_018P6O6_2g      4.5      1.0       6      1     0   
1       R7DC4sHDcklrk1s1K93FDA      4.5      4.0       0      0     0   
2       8kDLAf-muASQfs5zDXpiyw      4.5      5.0       0      0     0   
3       KupYGAYqAKVLP9cspQ-9TQ      4.5      5.0       1      1     0   
4       hl4dIQIKphmMWH59WrO5-g      4.5      4.0       2      1     1   
...                        ...      ...      ...     ...    ...   ...   
824895  wrqWvAdWD9YpB-1C2Xnp4w      4.5      2.0       0      4     0   
824896  TvXYbjdP1yiVqV4ixgKWsQ      4.5      5.0       1      0     0   
824897  dMhZvWaJAB957YIHjwKXWA      4.5      5.0       1      0     0   
824898  mTgQG-wCDdAW8ahnukggJg      4.5      5.0       0      0     0   
824899  x3Fel31bmcK1T6JzfcWHig      4.5      5.0       1      0     0   

                                                     text  \
0       The worst Chicken Parm. Sandwich I've ever eat...   
1       Zio's, previously known as Cesarina's is a lar...   
2       As an update to my previous review, we had tri...   
3       The little deli belongs in little Italy. Wonde...   
4       Very good food for very good prices. I had the...   
...                                                   ...   
824895  Very small menu.  Pizza is the ONLY food item ...   
824896  This place is great! The space is big with a n...   
824897  So first looking at the menu for this place yo...   
824898  I lived in CT for 10 years and CT style pizza ...   
824899  The pizza was thin crust and light. Great spot...   

                       date  score_sentimientos  categorizacion  
0       2014-05-25 21:52:30             -0.3561              -1  
1       2018-07-26 16:25:04              0.8287               1  
2       2018-04-28 00:32:12              0.9595               1  
3       2015-08-30 18:56:08              0.8238               1  
4       2011-10-28 20:06:00              0.8906               1  
...                     ...                 ...             ...  
824895  2021-11-04 02:43:27             -0.3609              -1  
824896  2021-11-04 13:28:42              0.9729               1  
824897  2022-01-02 03:35:40              0.9831               1  
824898  2021-11-26 22:55:22              0.9514               1  
824899  2021-11-14 16:53:07              0.6369               1  

[824900 rows x 12 columns]

Para este modelo solo se necesitan los usuarios que han calificado y las calificaciones de los usuarios:

In [4]:
df_ml = df_review.loc[:, ["stars_y", "business_id", "user_id"]]

In [5]:
df_ml.head()

stars_y             business_id                 user_id
0      1.0  0bPLkL0QhhPO5kt1_EXmNQ  z1Dfj8kz3KCArkXaIyaBIA
1      4.0  0bPLkL0QhhPO5kt1_EXmNQ  HvgKiuV36e9SzNqeA5zOfA
2      5.0  0bPLkL0QhhPO5kt1_EXmNQ  7BhiY0D84Lj04kjEWn5fIQ
3      5.0  0bPLkL0QhhPO5kt1_EXmNQ  0EjWviHaYwdaMaD8VBOHWA
4      4.0  0bPLkL0QhhPO5kt1_EXmNQ  E47ejL3krT1wG8NvgtJDgw

Se ven la cantidad de restaurantes y de usuarios:

In [77]:
df_ml["business_id"].nunique()

9187

In [78]:
df_ml["user_id"].nunique()

453535

Se crea la siguiente función para asignar a cada id un valor númerico con el propósito de una mejor visualizacion de los datos en las proximos códigos:

In [79]:
def asignar_clave_numerica(columna):
    claves = {}
    clave_actual = 1
    resultado = []

    for fila in columna:
        if fila not in claves:
            claves[fila] = clave_actual
            clave_actual += 1
        resultado.append(claves[fila])

    return resultado
df_ml["business_id"] = asignar_clave_numerica(df_ml["business_id"])
df_ml["user_id"] = asignar_clave_numerica(df_ml["user_id"])

In [80]:
df_ml["user_id"].nunique()

453535

Se toma una muestra para luego hacer una matriz:

In [93]:
muestra = df_ml.sample(n=12000, random_state=42)

In [94]:
muestra

stars_y  business_id  user_id
135270      3.0         1460   105952
623513      5.0         6933   367520
205919      5.0         2269   151186
758660      1.0         8479   425586
95497       5.0         1051    78138
...         ...          ...      ...
615101      5.0         6823   363642
648237      5.0         7165   378535
13885       3.0          160    12857
550399      5.0         6139    18756
734658      4.0         8179    44685

[12000 rows x 3 columns]

In [111]:
business_ids_unique = muestra['user_id'].unique()
print("Listado de IDs únicos en la muestra:")
for user_id in business_ids_unique:
    print(user_id)

Listado de IDs únicos en la muestra:
105952
367520
151186
425586
78138
233411
191974
25309
31749
295254
6560
101067
61578
347994
24103
281818
167281
205818
9693
157244
200354
278713
90925
412357
19604
42509
326991
66991
276203
50226
218644
296295
390167
268435
225177
146245
40551
65557
33275
2258
200963
16169
95111
398147
36980
242704
366308
219243
119956
271524
382924
194662
352299
226034
4832
29072
56066
164122
98099
385841
715
78110
55799
125541
35287
160466
88340
114197
27238
57447
19832
26887
124125
299290
79475
42080
119825
248173
403214
64585
213395
145887
21764
196524
101314
425031
45680
142100
429945
411343
10808
72355
283508
447835
158490
240646
238142
210524
389215
286544
42200
8130
13192
11845
148694
279557
53979
72994
334913
331521
120818
123998
350663
51102
291676
344204
85010
324743
378449
162425
17664
124987
147330
151793
48143
86657
2015
179790
444329
395624
37423
48415
324162
121794
116923
79809
329248
56764
14736
4929
186907
123801
62063
281622
174152
446931
339010
4

Se crea una Matriz donde las columnas son los restaurantes y las filas son los usuarios, el contenido de cada fila será la calificación que el usuario le ha dando al restaurante. En caso de no existir calificación se mostrará NaN.

En este tipo de modelos es normal que los datos útiles sean escasos, sin embargo es posible predecir la calificación de un usuario a traves de tecnicas como; factorización de matriz o similitud de coseno:

In [95]:
matrix = muestra.pivot_table(index='user_id', columns='business_id', values='stars_y')
matrix.head()

business_id  1     2     3     6     11    12    16    18    19    26    ...  \
user_id                                                                  ...   
8             5.0   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  ...   
20            NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  ...   
42            5.0   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  ...   
56            4.0   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  ...   
61            NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  ...   

business_id  9160  9165  9166  9168  9174  9176  9181  9182  9185  9187  
user_id                                                                  
8             NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
20            NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
42            NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
56            NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
61            NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  

[5 rows x 4251 columns]

Se mide la similitud de los usuarios, se usa la similitud de coseno:

In [96]:
from sklearn.metrics.pairwise import cosine_similarity

# Calcular la similitud coseno entre los usuarios
user_similarity_cosine = pd.DataFrame(cosine_similarity(matrix.fillna(0)), index=matrix.index, columns=matrix.index)

# Establecer el umbral de similitud (si es necesario)
user_similarity_threshold = 0.1

# Iterar sobre cada par de usuarios y mostrar sus valores de similitud
for user_id in user_similarity_cosine.index:
    for other_user_id, similarity_score in user_similarity_cosine.loc[user_id].items():
        # Verificar si la similitud está por encima del umbral y si el usuario no es el mismo que el de referencia
        if user_id != other_user_id and similarity_score > user_similarity_threshold:
            print(f'Usuario {user_id} es similar al usuario {other_user_id} con una similitud de {similarity_score}')

Usuario 8 es similar al usuario 42 con una similitud de 1.0
Usuario 8 es similar al usuario 56 con una similitud de 1.0
Usuario 20 es similar al usuario 76840 con una similitud de 1.0
Usuario 42 es similar al usuario 8 con una similitud de 1.0
Usuario 42 es similar al usuario 56 con una similitud de 1.0
Usuario 56 es similar al usuario 8 con una similitud de 1.0
Usuario 56 es similar al usuario 42 con una similitud de 1.0
Usuario 61 es similar al usuario 23341 con una similitud de 0.5443310539518174
Usuario 61 es similar al usuario 48498 con una similitud de 0.5443310539518174
Usuario 61 es similar al usuario 61987 con una similitud de 0.5443310539518174
Usuario 61 es similar al usuario 66198 con una similitud de 0.5443310539518174
Usuario 61 es similar al usuario 81903 con una similitud de 0.5443310539518174
Usuario 61 es similar al usuario 112281 con una similitud de 0.2721655269759087
Usuario 61 es similar al usuario 121875 con una similitud de 0.5443310539518174
Usuario 61 es simil

En la matriz de similitud del usuario, los valores varían de -1 a 1, donde -1 significa similitud opuesta y 1 significa similitud igual.

n = 10 significa los 10 usuarios más similares para el ID de usuario 412 (en este caso que lo vamos a tomar de ejemplo)

El filtrado colaborativo basado en usuarios hace recomendaciones basadas en usuarios con gustos similares, por lo que debemos establecer un umbral positivo. Aquí configuramos user_similarity_threshold en 0,3, lo que significa que un usuario debe tener un coeficiente de al menos 0,3 para ser considerado un usuario similar.


In [128]:
# Numero de usuarios similares
n = 10
userid = 61
# Umbral de similitud
user_similarity_threshold = 0.3

# Obtener el top n de usuarios similares basado en la similitud coseno
similar_users = user_similarity_cosine.loc[userid][user_similarity_cosine.loc[userid] > user_similarity_threshold].sort_values(ascending=False)[:n]

# Imprimir usuarios similares
print(f'Los usuarios similares para el usuario {userid} son:\n', similar_users)

Los usuarios similares para el usuario 61 son:
 user_id
61        1.000000
23341     0.544331
48498     0.544331
61987     0.544331
66198     0.544331
81903     0.544331
121875    0.544331
350744    0.544331
382765    0.544331
433310    0.544331
Name: 61, dtype: float64


El siguiente paso es reducir el grupo de elementos para simular una recomendación. Se eliminan las calificaciones del usuario seleccionado de la matriz original matrix y de las calificaciones de los usuarios similares.
A continuación, se eliminan los negocios que el usuario seleccionado ha visitado de las calificaciones de los usuarios similares.
Finalmente, se imprimen las calificaciones de los usuarios similares resultantes.

In [129]:
# ID del usuario seleccionado
picked_userid = 61
# Obtener las calificaciones de los usuarios similares
similar_user_ratings = matrix.loc[similar_users.index]

# Eliminar los negocios visitados por el usuario seleccionado
picked_user_ratings = matrix.drop(picked_userid, axis=0)

# Conservar solo las calificaciones de usuarios similares
similar_user_ratings = similar_user_ratings.drop(picked_userid, axis=0)

# Eliminar los negocios que el usuario seleccionado ha visitado
similar_user_ratings = similar_user_ratings.dropna(axis=1, how='all')

# Imprimir el DataFrame resultante
print("Calificaciones de los usuarios similares después de la selección:")
print(similar_user_ratings)

Calificaciones de los usuarios similares después de la selección:
business_id  8718
user_id          
23341         3.0
48498         4.0
61987         4.0
66198         3.0
81903         2.0
121875        3.0
350744        5.0
382765        5.0
433310        5.0


In [130]:
# Declarar un diccionario para el puntaje
item_score = {}

# Recorrer los restaurantes
for business_id, business_ratings in similar_user_ratings.items():
    # Inicializar variables para calcular el puntaje
    total_score = 0
    total_similarity = 0
    
    # Recorrer los usuarios similares
    for user_id, similarity_score in similar_users.items():
        # Obtener la calificación del restaurante por el usuario similar
        rating = business_ratings.get(user_id)
        if not pd.isna(rating):
            # Calcular el puntaje ponderado por la similitud del usuario
            total_score += similarity_score * rating
            total_similarity += similarity_score
    
    # Calcular el puntaje promedio para el restaurante
    if total_similarity > 0:
        item_score[business_id] = total_score / total_similarity

# Convertir el diccionario en un DataFrame
item_score_df = pd.DataFrame(item_score.items(), columns=['business_id', 'score'])

# Ordenar las recomendaciones por puntaje en orden descendente
ranked_recommendations = item_score_df.sort_values(by='score', ascending=False)

# Seleccionar las top m recomendaciones
m = 10
top_recommendations = ranked_recommendations.head(m)# Imprimir las top m recomendaciones
print("Top 10 recomendaciones para el usuario 61:")
top_recommendations


Top 10 recomendaciones para el usuario 61:


business_id     score
0         8718  3.777778